In [2]:
#Import required libraries and functions
from sahi import AutoDetectionModel
from sahi.utils.cv import read_image, read_image_as_pil
from sahi.utils.file import Path, increment_path, list_files, save_json, save_pickle, download_from_url
from sahi.predict import get_prediction, get_sliced_prediction, predict, agg_prediction, get_prediction_batched, get_sliced_prediction_batched, predict 
from sahi.prediction import visualize_object_predictions
from sahi.postprocess.utils import ObjectPredictionList, has_match, merge_object_prediction_pair
from IPython.display import Image
from numpy import asarray
from tqdm import tqdm
from PIL import Image
from sahi.prediction import ObjectPrediction, PredictionResult
from pathlib import Path
from multiprocessing import Pool, cpu_count
from torchvision.ops import nms, batched_nms, clip_boxes_to_image
import cv2
import os
import time
import json
import numpy as np
import time
import torch

In [3]:
# ==============================
# Annotation conversion (GOIS-style → VisDrone-in-COCO)
# ==============================

from pathlib import Path

# VisDrone 2019 category IDs (1..10)
VISDRONE_CATEGORIES = {
    1: "pedestrian",
    2: "people",
    3: "bicycle",
    4: "car",
    5: "van",
    6: "truck",
    7: "tricycle",
    8: "awning-tricycle",
    9: "bus",
    10: "motorcycle",
}

# Map common detector names → VisDrone IDs
NAME_TO_VISDRONE_ID = {
    "person": 1, "pedestrian": 1,
    "people": 2,
    "bicycle": 3,
    "car": 4,
    "van": 5,
    "truck": 6,
    "tricycle": 7,
    "awning-tricycle": 8,
    "bus": 9,
    "motorcycle": 10,
}

# If your detector uses COCO integer IDs, map the subset we care about → VisDrone
# COCO indices: 0-person, 1-bicycle, 2-car, 3-motorcycle, 5-bus, 7-truck
COCO_ID_TO_VISDRONE_ID = {
    0: 1,   # person → pedestrian
    1: 3,   # bicycle
    2: 4,   # car
    3: 10,  # motorcycle
    5: 9,   # bus
    7: 6,   # truck
    # (no direct COCO ids for: van, tricycle, awning-tricycle, people-group)
}

def get_image_id(coco_data, image_stem: str):
    """Return image id for a given file stem from dataset_json."""
    for image in coco_data["images"]:
        if Path(image["file_name"]).stem == image_stem:
            return image["id"]
    return None

def _bbox_to_xywh(bbox):
    """SAHI box or [x1,y1,x2,y2] → (xywh, area) with floats."""
    if hasattr(bbox, "to_xyxy"):
        x1, y1, x2, y2 = bbox.to_xyxy()
    else:
        x1, y1, x2, y2 = bbox
    w = max(0.0, float(x2) - float(x1))
    h = max(0.0, float(y2) - float(y1))
    return [float(x1), float(y1), w, h], w * h

def _remap_category(pred):
    """
    Decide VisDrone category_id for a SAHI ObjectPrediction:
      1) keep if already 1..10,
      2) else map by name,
      3) else map COCO int id subset,
      4) else return None (skip).
    """
    # id
    try:
        cid = int(pred.category.id)
    except Exception:
        cid = None
    # name
    try:
        cname = str(pred.category.name).lower()
    except Exception:
        cname = None

    if cid in VISDRONE_CATEGORIES:                 # already VisDrone ids
        return cid
    if cname in NAME_TO_VISDRONE_ID:               # name-based mapping
        return NAME_TO_VISDRONE_ID[cname]
    if cid in COCO_ID_TO_VISDRONE_ID:              # COCO→VisDrone subset
        return COCO_ID_TO_VISDRONE_ID[cid]
    return None

def preds_to_coco_visdrone(preds, image_id, score_threshold=0.0, warn_on_skip=False):
    """
    Convert a list of SAHI ObjectPrediction to COCO-style predictions
    using GOIS/VisDrone category ids (1..10).
    """
    coco_predictions = []
    skipped = 0
    for pred in preds:
        # score
        try:
            score = float(pred.score.value)
        except Exception:
            score = float(getattr(pred, "score", 0.0))
        if score < score_threshold:
            continue

        # category mapping
        cat_id = _remap_category(pred)
        if cat_id is None:
            skipped += 1
            continue

        # bbox
        bbox_xywh, area = _bbox_to_xywh(pred.bbox)

        coco_predictions.append({
            "image_id": int(image_id),
            "category_id": int(cat_id),
            "bbox": [round(b, 2) for b in bbox_xywh],  # COCO = [x,y,w,h]
            "score": round(score, 6),
            "segmentation": [],
            "iscrowd": 0,
            "area": round(float(area), 2),
        })
    if warn_on_skip and skipped:
        print(f"[preds_to_coco_visdrone] Skipped {skipped} prediction(s) due to unmapped categories.")
    return coco_predictions

In [13]:
#create the model instance

#baseline_yolo_model_path = 'models/baseline/yolov8n.pt'
pretrained_yolo_model_path = 'models/yolov8/last.pt'
#fined_tuned__mixed_yolov8_model_path = 'models/fine-tuned/mixed/YOLOv8n/last.pt'
detection_model = AutoDetectionModel.from_pretrained(
        model_type='yolov8',
        model_path=baseline_yolo_model_path,
        confidence_threshold=0.25,
        device="cuda:0", # or 'cpu'
)

In [5]:
#functions to set the overlap ratio and slice size as per detected objects count in each slice
def get_slice_parameters(object_density, slice_size):
    
    if object_density >= 50:
        #slice_size = min_dim // 4
        slice_width = slice_size
        slice_height = slice_size
        overlap_width_ratio = 0.5
        overlap_height_ratio = 0.5
    elif 25 <= object_density < 50:
        #slice_size = min_dim // 2
        slice_width = slice_size
        slice_height = slice_size
        overlap_width_ratio = 0.25
        overlap_height_ratio = 0.25
    elif 10 <= object_density < 25:
        #slice_size = min_dim // 2
        slice_width = slice_size
        slice_height = slice_size
        overlap_width_ratio = 0.15
        overlap_height_ratio = 0.15
    else:
        return

    return slice_width, slice_height, overlap_width_ratio, overlap_height_ratio

In [9]:
# Apply Non-Maximum Suppression (NMS)
def apply_nms(detections, iou_threshold=0.5):
    boxes, scores, labels = [], [], []
    for det in detections:
        boxes.append(det.bbox.to_xyxy())
        scores.append(det.score.value)
        labels.append(det.category.id)
    boxes = torch.tensor(boxes, dtype=torch.float32)
    scores = torch.tensor(scores, dtype=torch.float32)
    labels = torch.tensor(labels)

    keep_indices = []
    unique_labels = labels.unique()
    for label in unique_labels:
        idxs = (labels == label).nonzero(as_tuple=False).squeeze(1)
        class_boxes = boxes[idxs]
        class_scores = scores[idxs]
        keep = nms(class_boxes, class_scores, iou_threshold)
        keep_indices.extend(idxs[keep].tolist())

    return [detections[i] for i in keep_indices]

In [6]:
#convert final predictions after NMS merge to COCO format
def merged_preds_to_coco(preds, image_id):
    coco_predictions = []
    for pred in preds:
        try:
            coco = pred.to_coco_prediction(image_id=image_id)
            coco_dict = {
                "image_id": coco.image_id,
                "bbox": coco.bbox,
                "score": coco.score,
                "category_id": coco.category_id,
                "segmentation": coco.segmentation,
                "iscrowd": coco.iscrowd,
                "area": coco.area,
            }
            # Optionally include category_name (not used in COCO eval)
            # coco_dict["category_name"] = coco.category_name

            # Only add if bbox is valid (non-empty)
            if coco_dict["bbox"]:
                coco_predictions.append(coco_dict)
        except Exception as e:
            print(f"Failed to convert to COCO dict: {e}")
    return coco_predictions

In [7]:
# Function to get image details by image_id
def get_image_id(coco_data, image_name):
    for image in coco_data["images"]:
        file_name = Path(image['file_name']).stem
        if file_name == image_name:
            return image['id']
    return None

In [10]:
def predict_multilevel_fine_sliced_images(input_folder, dataset_json_path, detection_model, base_slice_size=512):

    print("\n***********************************************")
    print("Adaptive MultiLevel SAHI Prediction")
    print("*************************************************")
    
    name = "exp"
    save_dir = Path(increment_path(Path("sliced_predictions") / name, exist_ok=False))
    os.makedirs(save_dir, exist_ok=True)

    if dataset_json_path:
        with open(dataset_json_path, "r") as file:
            data = json.load(file)
        
    vis_params = {
        "bbox_thickness": 2,
        "text_size": 0.5,
        "text_thickness": 1,
        "hide_labels": False,
        "hide_conf": False,
        "format": "png"
    }

    image_files = [
        f for f in os.listdir(input_folder)
        if f.lower().endswith((".jpg", ".jpeg", ".png"))
    ]

    print(f"\nRunning fine slicing prediction on {len(image_files)} image(s)...")
    total_prediction_time = 0.0
    grand_total_predictions = 0
    all_coco_preds = []

    for filename in image_files:
        image_path = os.path.join(input_folder, filename)
        image_pil = Image.open(image_path).convert("RGB")
        image_np = np.array(image_pil)
        image_h, image_w = image_np.shape[:2]
        filename_wo_ext = Path(filename).stem
        total_prediction_count = 0
        print("*****************************************")
        print("File Name: ", filename_wo_ext)
        print("*****************************************")
        
        img_id = get_image_id(data, filename_wo_ext) if dataset_json_path else None
        all_object_predictions = []

        #Base prediction
        t0 = time.time()
        intial_prediction = get_prediction(image_path, detection_model)
        t_base = (time.time() - t0)
        print(f"Base pred time: {t_base * 1000:.2f} ms")
        total_prediction_time += t_base
        print(f"Total Based pred time: {total_prediction_time * 1000:.2f} ms")
        full_preds = intial_prediction.object_prediction_list
        full_object_density = len(full_preds)
        print("Full Image Object Density:", full_object_density)

        for pred in full_preds:
            all_object_predictions.append(pred)
            
        total_prediction_count += len(all_object_predictions)
    
        # Split image into 2x2 grid
        grid_h, grid_w = image_h // 2, image_w // 2

        for row in range(2):
            for col in range(2):
                x1, y1 = col * grid_w, row * grid_h
                x2, y2 = min(x1 + grid_w, image_w), min(y1 + grid_h, image_h)
                sub_img = image_pil.crop((x1, y1, x2, y2))
                print("Cropped Image Dimension:", x1, y1, x2, y2)

                time_start = time.time()
                base_pred = get_prediction(sub_img, detection_model)
                time_end = time.time() - time_start
                
                print("Initial Prediction time is: {:.2f} ms".format(time_end * 1000))

                coarse_preds = base_pred.object_prediction_list
                object_density = len(coarse_preds)
                print("Slice Object Density:", object_density)
                
                slice_params = get_slice_parameters(object_density, base_slice_size)
            
                iteration_time = time_end
                
                preds = coarse_preds.copy()
                
                if slice_params:
                    slice_width, slice_height, overlap_w, overlap_h = slice_params
                    print("********* Slice Parameters ***********")
                    print("Slice Width: ", slice_width)
                    print("Slice Height: ", slice_height)
                    print("Overlap Width Ratio: ", overlap_w)
                    print("Overlap Height Ratio: ", overlap_h)

                    time_start_slice = time.time()
                    sliced_pred = get_sliced_prediction(
                        sub_img,
                        detection_model,
                        slice_height=slice_height,
                        slice_width=slice_width,
                        overlap_height_ratio=overlap_h,
                        overlap_width_ratio=overlap_w,
                        postprocess_type="NMS",
                        postprocess_match_metric="IOU",
                        postprocess_match_threshold=0.3,
                        postprocess_min_area=16,
                        verbose=0
                    )
                    time_end_slice = time.time() - time_start_slice
                    print("Sliced Prediction time is: {:.2f} ms".format(time_end_slice * 1000))
                    
                    iteration_time += time_end_slice
                    fine_preds = sliced_pred.object_prediction_list
                    print("Pre Adaptive Slicing: ", len(preds))
                    preds.extend(fine_preds)
                    print("Post Adaptive Slicing: ", len(preds))
                else:
                    print("Prediction time is: {:.2f} ms".format(time_end * 1000))

                total_prediction_time += iteration_time
                
                #Offset bounding boxes back to original image space
                for pred in preds:
                    pred.bbox.minx += x1
                    pred.bbox.maxx += x1
                    pred.bbox.miny += y1
                    pred.bbox.maxy += y1
                    all_object_predictions.append(pred)
        
                total_prediction_count += len(preds)

        print("________________________________________________")

        print("Total Prediction Count (Crop+Slice): ", len(all_object_predictions))
        
        # Merge all predictions for image
        merged_preds = apply_nms(all_object_predictions, iou_threshold=0.5)
        
        #object_prediction_list = ObjectPredictionList(all_object_predictions)
        #merged_keep = truncated_nms_merge(object_prediction_list.totensor())
        #selected_object_predictions = object_prediction_list[merged_keep].tolist()
        #if not isinstance(selected_object_predictions, list):
        #    selected_object_predictions = [selected_object_predictions]
        
        # Convert merged predictions to COCO format
        if dataset_json_path:
            coco_preds = preds_to_coco_visdrone(
                merged_preds,
                image_id=img_id,
                score_threshold=0.0,      # or e.g. 0.001 to mirror eval setup
                warn_on_skip=True
            )
            all_coco_preds.extend(coco_preds)
            
        # Visualization
        visualize_object_predictions(
            image=np.ascontiguousarray(image_pil),
            object_prediction_list=merged_preds,
            rect_th=vis_params["bbox_thickness"],
            text_size=vis_params["text_size"],
            text_th=vis_params["text_thickness"],
            hide_labels=vis_params["hide_labels"],
            hide_conf=vis_params["hide_conf"],
            output_dir=save_dir,
            file_name=filename_wo_ext,
            export_format=vis_params["format"]
        )

        grand_total_predictions += total_prediction_count

    if dataset_json_path:
        save_path = str(save_dir / "result.json")
        save_json(all_coco_preds, save_path)
   
    print(f"\nCompleted {len(image_files)} images.")
    print("Total Prediction Count (Before NMS Merge): ", grand_total_predictions)
    print("Total Prediction Count (After Final NMS Merge): ", len(merged_preds))
    print("Total Prediction time for all images is: {:.2f} ms".format(total_prediction_time * 1000))
    print(f"Prediction results are successfully exported to {save_dir}")


#### **GOIS Base Dataset Evaluation**

In [10]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS) -->gois compatible renew code
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/train_subset/VisDrone2019-DET-train-15_Subset970-Images/images'
json_path = "../GOIS/data/ground_truth/subset_traintest_ground_truth_coco.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1518 image(s)...
*****************************************
File Name:  9999972_00000_d_0000084
*****************************************


/mmfs1/cm/shared/apps_local/python/3.11/envs/torch11.8/lib/python3.9/site-packages/torch/nn/modules/conv.py:456: UserWarning: Applied workaround for CuDNN issue, install nvrtc.so (Triggered internally at ../aten/src/ATen/native/cudnn/Conv_v8.cpp:80.)
  return F.conv2d(input, weight, bias, self.stride,


Base pred time: 570.58 ms
Total Based pred time: 570.58 ms
Full Image Object Density: 27
Cropped Image Dimension: 0 0 958 539
Initial Prediction time is: 10.43 ms
Slice Object Density: 11
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 15
POST PROCESS:  NMS
Confidence Score:  0.3
Original Prediction Count 44
Final Bounding Box Count (NMS):  13
Final Bounding Box Count (NMS):  2
Sliced Prediction time is: 140.81 ms
Pre Adaptive Slicing:  11
Post Adaptive Slicing:  26
Cropped Image Dimension: 958 0 1916 539
Initial Prediction time is: 9.47 ms
Slice Object Density: 4
Prediction time is: 9.47 ms
Cropped Image Dimension: 0 539 958 1078
Initial Prediction time is: 9.40 ms
Slice Object Density: 7
Prediction time is: 9.40 ms
Cropped Image Dimension: 958 539 1916 1078
Initial Prediction time is: 9.41 ms
Slice Object Density: 7
Prediction time is: 9.41 ms
_______________________________________

In [11]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path '../GOIS/data/ground_truth/subset_traintest_ground_truth_coco.json' --result_json_path './sliced_predictions/exp1062/result.json'

loading annotations into memory...
Done (t=0.32s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.06s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=17.07s).
Accumulating evaluation results...
DONE (t=0.35s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.041
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.084
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.033
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.072
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.136
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.078
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.032
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.076
 Average Precision  (AP) @[ IoU=0.50:0.95 | 

In [15]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS) -->gois compatible renew code
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/train_subset/VisDrone2019-DET-train-15_Subset970-Images/images'
json_path = "../GOIS/data/ground_truth/subset_traintest_ground_truth_coco.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1518 image(s)...
*****************************************
File Name:  9999972_00000_d_0000084
*****************************************
Base pred time: 499.16 ms
Total Based pred time: 499.16 ms
Full Image Object Density: 7
Cropped Image Dimension: 0 0 958 539
Initial Prediction time is: 11.61 ms
Slice Object Density: 3
Prediction time is: 11.61 ms
Cropped Image Dimension: 958 0 1916 539
Initial Prediction time is: 11.24 ms
Slice Object Density: 2
Prediction time is: 11.24 ms
Cropped Image Dimension: 0 539 958 1078
Initial Prediction time is: 10.95 ms
Slice Object Density: 3
Prediction time is: 10.95 ms
Cropped Image Dimension: 958 539 1916 1078
Initial Prediction time is: 10.87 ms
Slice Object Density: 2
Prediction time is: 10.87 ms
________________________________________________
Total Prediction Count (Crop+Slice)

In [16]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path '../GOIS/data/ground_truth/subset_traintest_ground_truth_coco.json' --result_json_path './sliced_predictions/exp1063/result.json'

loading annotations into memory...
Done (t=0.32s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.02s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=4.80s).
Accumulating evaluation results...
DONE (t=0.14s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.018
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.035
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.015
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.027
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.078
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.066
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.013
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.042
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [17]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path '../GOIS/data/ground_truth/subset_traintest_ground_truth_coco.json' --result_json_path './sliced_predictions/exp1063/result.json' --max_detections 100

loading annotations into memory...
Done (t=0.34s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.02s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=4.75s).
Accumulating evaluation results...
DONE (t=0.14s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=100 ] = 0.018
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=100 ] = 0.035
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=100 ] = 0.015
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=100 ] = 0.027
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=100 ] = 0.078
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=100 ] = 0.066
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=100 ] = 0.013
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=100 ] = 0.042
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

#### **Mix of 500 images**

In [18]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/mix/v1/images'
json_path = "../GOIS/data/ground_truth/500_mix_ground_truth_coco.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 500 image(s)...
*****************************************
File Name:  0000320_00300_d_0000004
*****************************************
Base pred time: 25.40 ms
Total Based pred time: 25.40 ms
Full Image Object Density: 29
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 9.84 ms
Slice Object Density: 22
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 6
POST PROCESS:  NMS
Confidence Score:  0.3
Original Prediction Count 53
Final Bounding Box Count (NMS):  11
Final Bounding Box Count (NMS):  12
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 75.71 ms
Pre Adaptive Slicing:  22
Post Adaptive Slicing:  47
Cropped Image Dimension: 680 0 1360 382
Initial Predi

In [19]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path '../GOIS/data/ground_truth/500_mix_ground_truth_coco.json' --result_json_path './sliced_predictions/exp1064/result.json'

loading annotations into memory...
Done (t=0.03s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=1.38s).
Accumulating evaluation results...
DONE (t=0.04s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.014
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.027
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.011
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.015
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.093
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.170
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.006
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.046
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [11]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './single_test/images'
json_path = "../GOIS/data/ground_truth/subset_ground_truth_coco_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 27.57 ms
Total Based pred time: 27.57 ms
Full Image Object Density: 5
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 9.57 ms
Slice Object Density: 2
Prediction time is: 9.57 ms
Cropped Image Dimension: 680 0 1360 382
Initial Prediction time is: 9.22 ms
Slice Object Density: 1
Prediction time is: 9.22 ms
Cropped Image Dimension: 0 382 680 764
Initial Prediction time is: 9.00 ms
Slice Object Density: 1
Prediction time is: 9.00 ms
Cropped Image Dimension: 680 382 1360 764
Initial Prediction time is: 8.95 ms
Slice Object Density: 1
Prediction time is: 8.95 ms
________________________________________________
Total Prediction Count (Crop+Slice):  10
[preds_to

In [12]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path '../GOIS/data/ground_truth/subset_ground_truth_coco_990.json' --result_json_path './sliced_predictions/exp1066/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.00s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [14]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './single_test/images'
json_path = "../GOIS/data/ground_truth/subset_ground_truth_coco_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


***********************************************
Adaptive MultiLevel SAHI Prediction
*************************************************

Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 89.61 ms
Total Based pred time: 89.61 ms
Full Image Object Density: 5
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 9.45 ms
Slice Object Density: 2
Prediction time is: 9.45 ms
Cropped Image Dimension: 680 0 1360 382
Initial Prediction time is: 9.18 ms
Slice Object Density: 1
Prediction time is: 9.18 ms
Cropped Image Dimension: 0 382 680 764
Initial Prediction time is: 10.49 ms
Slice Object Density: 1
Prediction time is: 10.49 ms
Cropped Image Dimension: 680 382 1360 764
Initial Prediction time is: 8.97 ms
Slice Object Density: 1
Prediction time is: 8.97 ms
________________________________________________
Total Prediction Count (Crop+Slice):  10
[preds_

In [15]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path '../GOIS/data/ground_truth/subset_ground_truth_coco_990.json' --result_json_path './sliced_predictions/exp1067/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.00s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | a